In [6]:
import pandas as pd

# Load dataset
train_csv = "/home/nogaschw/outfit-transformer-main/Fashion Rec -Style and Event - Data/train.csv"
df_train = pd.read_csv(train_csv, header=0, delimiter=",", low_memory=False)

# Print the actual column names
print("Column names detected in the dataset:", df_train.columns.tolist())


Column names detected in the dataset: ['image_path', 'category', 'event']


In [7]:
df_train.rename(columns={"category": "style"}, inplace=True)
print("✅ Column names after renaming:", df_train.columns.tolist())


✅ Column names after renaming: ['image_path', 'style', 'event']


In [8]:
# Style Labels Dictionary (Kobayashi’s Color Image Scale)
style_mapping = {
    0: "Romantic",
    1: "Pretty",
    2: "Clear",
    3: "Cool-Casual",
    4: "Natural",
    5: "Formal",
    6: "Elegant",
    7: "Modern",
    8: "Chic",
    9: "Dandy",
    10: "Classic",
    11: "Dynamic",
    12: "Ethnic",
    13: "Gorgeous"
}

# Apply the mapping to the dataset
df_train["style"] = df_train["style"].map(style_mapping)

# Verify distribution
print(df_train["style"].value_counts())


style
Ethnic         42612
Dynamic        41200
Modern         35927
Natural        32545
Romantic       24782
Classic        22921
Clear          21264
Pretty         20769
Gorgeous       20548
Chic           19475
Elegant        11805
Dandy           9033
Cool-Casual     7983
Formal          6311
Name: count, dtype: int64


In [9]:
event_mapping = {
    0: "Concert",
    1: "Graduation",
    2: "Meeting",
    3: "Mountain Trip",
    4: "Picnic",
    5: "Sea Holiday",
    6: "Ski Holiday",
    7: "Wedding",
    8: "Conference",
    9: "Exhibition",
    10: "Fashion Show",
    11: "Protest",
    12: "Sports Event",
    13: "Theater/Dance"
}

# Apply the mapping to the dataset
df_train["event"] = df_train["event"].map(event_mapping)

# Verify distribution
print(df_train["event"].value_counts())


event
Wedding          118017
Concert           50874
Graduation        47325
Mountain Trip     27451
Ski Holiday       19171
Protest           14183
Conference        14015
Picnic             9548
Exhibition         7363
Fashion Show       3478
Sea Holiday        3309
Sports Event       2225
Meeting             216
Name: count, dtype: int64


 Extract Image Embeddings for df_train
We need to generate ResNet embeddings for images in df_train.

In [ ]:
import torch
import torchvision.transforms as transforms
from torchvision import models
from torchvision.models import ResNet50_Weights  # ✅ Use correct weights
from PIL import Image
import os
import pickle
import pandas as pd

# 🔹 Set device (GPU or CPU)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"✅ Using device: {device}")

# 🔹 Load ResNet50 Model (Updated to avoid warnings)
resnet = models.resnet50(weights=ResNet50_Weights.IMAGENET1K_V1)  # ✅ Correct way to load weights
resnet = resnet.to(device)
resnet.eval()

# 🔹 Define Image Preprocessing
transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])


# 🔹 Extract image filenames
df_train["image_id"] = df_train["image_path"].apply(lambda x: x.split("/")[-1])

# 🔹 Define dictionary to store embeddings
train_embeddings = {}

# 🔹 Extract embeddings for each image
for idx, row in df_train.iterrows():
    image_path = row["image_path"]
    
    try:
        # Load image
        img = Image.open(image_path).convert("RGB")
        img = transform(img).unsqueeze(0).to(device)  # Apply transformations
        
        # Extract features
        with torch.no_grad():
            features = resnet(img)

        # Store embeddings
        train_embeddings[row["image_id"]] = {"image_features": features.cpu().numpy()}
    
    except Exception as e:
        print(f"❌ Error processing {image_path}: {e}")

# 🔹 Save extracted embeddings
output_embeddings = "/home/nogaschw/outfit-transformer-main/Fashion Rec -Style and Event - Data/train_embeddings.pkl"

with open(output_embeddings, "wb") as f:
    pickle.dump(train_embeddings, f)

print(f"✅ Feature extraction complete! Saved to {output_embeddings}")


 Step 1: Load the Data and Prepare the Features
First, we need to load the filtered dataset and extract the deep features (ResNet50 embeddings) + labels.

In [28]:
filtered_csv = "/home/nogaschw/outfit-transformer-main/Fashion Rec -Style and Event - Data/style.csv"
df = pd.read_csv(filtered_csv)

In [87]:
embeddings_file = "/home/nogaschw/outfit-transformer-main/Fashion Rec -Style and Event - Data/polyvore_embeddings.pkl"
with open(embeddings_file, "rb") as f:
    embeddings = pickle.load(f)

In [88]:
embeddings = {int(key.replace('.jpg', '')): value['image_features'] for key, value in embeddings.items()}

In [31]:
# Create a dictionary with image ID as key and style as value
image_style_dict = {int(row['image_path'].split('/')[-1].replace('.jpg', '')): row['style'] for _, row in df.iterrows()}

In [48]:
combined_styles = []
combined_embeddings = []

# Iterate through the embeddings dictionary
for image_id, data in embeddings.items():
    if image_id in image_style_dict:
        combined_embeddings.append(embeddings[image_id])
        combined_styles.append(image_style_dict[image_id])

In [61]:
import pickle
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, classification_report

# ✅ Load the cleaned dataset
filtered_train_csv = "/home/nogaschw/outfit-transformer-main/Fashion Rec -Style and Event - Data/train_filtered.csv"
df_train = pd.read_csv(filtered_train_csv)
df_train.rename(columns={"category": "style"}, inplace=True)

# ✅ Load the existing embeddings
embeddings_file = "/home/nogaschw/outfit-transformer-main/Fashion Rec -Style and Event - Data/train_embeddings.pkl"
with open(embeddings_file, "rb") as f:
    embeddings = pickle.load(f)

# ✅ Extract image IDs
df_train["image_id"] = df_train["image_path"].apply(lambda x: x.split("/")[-1])

# ✅ Keep only images that have embeddings
df_train = df_train[df_train["image_id"].isin(embeddings.keys())]

# ✅ Extract features and labels
X = np.array([embeddings[img]["image_features"].flatten() for img in df_train["image_id"]])
y_style = combined_styles  # Style labels
y_event = df_train["event"].values  # Event labels

# ✅ Normalize features for better classification
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

# ✅ Split data into train & test sets (80% train, 20% test)
X_train_style, X_test_style, y_train_style, y_test_style = train_test_split(combined_embeddings, y_style, test_size=0.6, random_state=42)
X_train, X_test, y_train_event, y_test_event = train_test_split(X_scaled, y_event, test_size=0.2, random_state=42)

print(f"✅ Data prepared! Training samples: {len(X_train)}, Testing samples: {len(X_test)}")


✅ Data prepared! Training samples: 216243, Testing samples: 54061


 Step 2: Train Style & Event Classifiers
We'll use Random Forest Classifiers to train on both Style and Event labels.

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset
from torchmetrics.classification import MulticlassF1Score, MulticlassAUROC, MulticlassAccuracy

In [8]:
os.getcwd()

'/sise/home/nogaschw/outfit-transformer-main/Fashion Rec -Style and Event'

In [ ]:
import sys
import os

sys.path.append(os.path.join(os.getcwd(), ".."))
from src.models.Classifier import ImageEmbeddingClassifier

In [18]:
style_classifier = ImageEmbeddingClassifier()

In [56]:
# Initialize the model, loss function, and optimizer
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
style_classifier = ImageEmbeddingClassifier().to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(style_classifier.parameters(), lr=0.001)

In [57]:
style_classifier.to(device)

ImageEmbeddingClassifier(
  (fc1): Linear(in_features=1000, out_features=512, bias=True)
  (relu1): ReLU()
  (fc2): Linear(in_features=512, out_features=512, bias=True)
  (relu2): ReLU()
  (fc3): Linear(in_features=512, out_features=14, bias=True)
)

In [73]:
def training(model, X_train, y_train, X_test, y_test, batch_size=64):
    X_train = torch.tensor(X_train, dtype=torch.float32)  # Convert to float tensor
    y_train = torch.tensor(y_train, dtype=torch.long)  # Convert to long tensor (for classification)

    # Now create the dataset
    train_dataset = TensorDataset(X_train, y_train)
    train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
    max_auc = 0
    # Training loop
    num_epochs = 20
    for epoch in range(num_epochs):
        model.train()  # Set model to training mode
        total_loss = 0
        correct = 0
        total = 0
        for inputs, labels in train_loader:
            inputs, labels = inputs.to(device), labels.to(device)  # Move to GPU if available

            optimizer.zero_grad()  # Reset gradients
            outputs = model(inputs)  # Forward pass
            loss = criterion(outputs, labels)  # Compute loss

            loss.backward()  # Backpropagation
            optimizer.step()  # Update weights

            total_loss += loss.item()

            # Compute accuracy
            _, predicted = torch.max(outputs, 1)  # Get class with highest score
            correct += (predicted == labels).sum().item()
            total += labels.size(0)

        print(f"Epoch [{epoch+1}/{num_epochs}] - "
            f"Loss: {total_loss / len(train_loader):.4f}, "
            f"Accuracy: {correct / total:.4%}, ")
        now_auc = evaluate_model(model=model, X_test=X_test, y_test=y_test)
        if max_auc < now_auc:
            print(now_auc)
            max_auc = now_auc
            max_model = model
    print("Training complete!")
    return max_model

In [69]:
def evaluate_model(model, X_test, y_test, batch_size=64, num_classes=14, device="cuda"):
    """
    Evaluate a PyTorch model on a test dataset and return F1-score and ROC-AUC.
    
    Args:
        model (torch.nn.Module): The trained PyTorch model.
        test_dataset (torch.utils.data.Dataset): The test dataset.
        batch_size (int): Batch size for DataLoader.
        num_classes (int): Number of classes in the classification task.
        device (str): "cuda" or "cpu".
    
    Returns:
        tuple: (F1-score, AUC score)
    """
    X_test = torch.tensor(X_test, dtype=torch.float32)  # Convert to float tensor
    y_test = torch.tensor(y_test, dtype=torch.long)  # Convert to long tensor (for classification)

    # Now create the dataset
    test_dataset = TensorDataset(X_test, y_test)
    # DataLoader for test set
    test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)

    # Move model to device and set to evaluation mode
    model.to(device)
    model.eval()

    # Initialize metrics
    f1_metric = MulticlassF1Score(num_classes=num_classes, average="macro").to(device)
    auc_metric = MulticlassAUROC(num_classes=num_classes, average="macro").to(device)
    acc_metric = MulticlassAccuracy(num_classes=num_classes, average="macro").to(device)

    all_preds = []
    all_labels = []
    all_probs = []

    with torch.no_grad():  # No gradient computation needed
        for inputs, labels in test_loader:
            inputs, labels = inputs.to(device), labels.to(device)

            outputs = model(inputs)  # Forward pass
            probs = torch.softmax(outputs, dim=1)  # Convert logits to probabilities
            preds = torch.argmax(probs, dim=1)  # Get class predictions

            all_preds.append(preds)
            all_labels.append(labels)
            all_probs.append(probs)

    # Convert to tensors
    all_preds = torch.cat(all_preds)
    all_labels = torch.cat(all_labels)
    all_probs = torch.cat(all_probs)

    # Compute F1 and AUC
    acc_score = acc_metric(all_preds, all_labels).item()
    f1_score = f1_metric(all_preds, all_labels).item()
    auc_score = auc_metric(all_probs, all_labels).item()
    
    return auc_score

### Event

In [ ]:
style_classifier_trained = training(model=style_classifier, X_train=X_train, y_train=y_train_event, X_test=X_test, y_test=y_test_event)

Epoch [1/20] - Loss: 0.6966, Accuracy: 76.3553%, 
0.508836030960083
Epoch [2/20] - Loss: 0.5906, Accuracy: 79.7487%, 
0.5121111869812012
Epoch [3/20] - Loss: 0.5515, Accuracy: 81.0389%, 
Epoch [4/20] - Loss: 0.5215, Accuracy: 82.0327%, 
Epoch [5/20] - Loss: 0.4984, Accuracy: 82.7791%, 
Epoch [6/20] - Loss: 0.4764, Accuracy: 83.4358%, 
Epoch [7/20] - Loss: 0.4566, Accuracy: 84.1664%, 
0.5147968530654907
Epoch [8/20] - Loss: 0.4415, Accuracy: 84.5896%, 
Epoch [9/20] - Loss: 0.4257, Accuracy: 85.1029%, 
Epoch [10/20] - Loss: 0.4110, Accuracy: 85.6546%, 
0.5158292055130005
Epoch [11/20] - Loss: 0.3969, Accuracy: 86.1258%, 
Epoch [12/20] - Loss: 0.3841, Accuracy: 86.5697%, 
Epoch [13/20] - Loss: 0.3718, Accuracy: 86.9938%, 
Epoch [14/20] - Loss: 0.3618, Accuracy: 87.2810%, 
Epoch [15/20] - Loss: 0.3505, Accuracy: 87.6815%, 
Epoch [16/20] - Loss: 0.3402, Accuracy: 88.0657%, 
Epoch [17/20] - Loss: 0.3334, Accuracy: 88.3446%, 
Epoch [18/20] - Loss: 0.3229, Accuracy: 88.6322%, 
Epoch [19/20] - 

In [ ]:
import json
import torch
from torch.utils.data import DataLoader, TensorDataset

def save_transformed_embeddings(model, id_embedding_dict, output_file, batch_size=128, device='cuda'):
    model.eval()  # Set model to evaluation mode
    
    # Convert dictionary to list of (id, tensor) pairs
    ids = list(id_embedding_dict.keys())
    embeddings = torch.tensor(list(id_embedding_dict.values()), dtype=torch.float32, device=device)

    # Use DataLoader for batch processing
    dataset = TensorDataset(embeddings)
    dataloader = DataLoader(dataset, batch_size=batch_size, shuffle=False)

    transformed_dict = {}
    with torch.no_grad():  # No gradients needed for inference
        batch_start = 0
        for i, batch in enumerate(dataloader):
            if i % 100 == 0:
                print(f'{i} / {len(dataloader)}')
            batch_embeddings = batch[0]  # Extract batch data
            transformed_batch = model(batch_embeddings, return_hidden=True)  # Forward pass through the model
            
            # Store transformed embeddings
            for i, emb in enumerate(transformed_batch):
                transformed_dict[ids[batch_start + i]] = emb.cpu().tolist()  # Convert tensor to list
            
            batch_start += len(batch_embeddings)

    # Save to JSON file
    with open(output_file, 'w') as f:
        json.dump(transformed_dict, f, indent=4)

    print(f"Saved transformed embeddings to {output_file}")
    return transformed_dict

# Assuming `model` is your trained neural network
save_transformed_embeddings(style_classifier_trained, embeddings, "item_event.json", batch_size=32)


## Style

In [74]:
style_classifier_trained = training(model=style_classifier, X_train=X_train_style, y_train=y_train_style, X_test=X_test_style, y_test=y_test_style)

Epoch [1/20] - Loss: 0.2842, Accuracy: 89.3298%, 
0.8081276416778564
Epoch [2/20] - Loss: 0.2872, Accuracy: 89.5214%, 
Epoch [3/20] - Loss: 0.2820, Accuracy: 89.6449%, 
0.8098973035812378
Epoch [4/20] - Loss: 0.2894, Accuracy: 89.3576%, 
Epoch [5/20] - Loss: 0.2690, Accuracy: 90.0117%, 
0.810808002948761
Epoch [6/20] - Loss: 0.2781, Accuracy: 89.7790%, 
0.810809850692749
Epoch [7/20] - Loss: 0.2801, Accuracy: 89.7991%, 
Epoch [8/20] - Loss: 0.2728, Accuracy: 89.8958%, 
Epoch [9/20] - Loss: 0.2653, Accuracy: 90.2770%, 
0.812696635723114
Epoch [10/20] - Loss: 0.2898, Accuracy: 89.5223%, 
Epoch [11/20] - Loss: 0.2770, Accuracy: 89.8881%, 
Epoch [12/20] - Loss: 0.2845, Accuracy: 89.8010%, 
Epoch [13/20] - Loss: 0.2682, Accuracy: 90.1477%, 
Epoch [14/20] - Loss: 0.2561, Accuracy: 90.5250%, 
Epoch [15/20] - Loss: 0.2628, Accuracy: 90.3124%, 
Epoch [16/20] - Loss: 0.2704, Accuracy: 90.0634%, 
Epoch [17/20] - Loss: 0.2621, Accuracy: 90.2875%, 
Epoch [18/20] - Loss: 0.2599, Accuracy: 90.2980%, 

In [89]:
import json
import torch
from torch.utils.data import DataLoader, TensorDataset

def save_transformed_embeddings(model, id_embedding_dict, output_file, batch_size=128, device='cuda'):
    model.eval()  # Set model to evaluation mode
    
    # Convert dictionary to list of (id, tensor) pairs
    ids = list(id_embedding_dict.keys())
    embeddings = torch.tensor(list(id_embedding_dict.values()), dtype=torch.float32, device=device)

    # Use DataLoader for batch processing
    dataset = TensorDataset(embeddings)
    dataloader = DataLoader(dataset, batch_size=batch_size, shuffle=False)

    transformed_dict = {}
    with torch.no_grad():  # No gradients needed for inference
        batch_start = 0
        for i, batch in enumerate(dataloader):
            if i % 100 == 0:
                print(f'{i} / {len(dataloader)}')
            batch_embeddings = batch[0]  # Extract batch data
            transformed_batch = model(batch_embeddings, return_hidden=True)  # Forward pass through the model
            
            # Store transformed embeddings
            for i, emb in enumerate(transformed_batch):
                transformed_dict[ids[batch_start + i]] = emb.cpu().tolist()  # Convert tensor to list
            
            batch_start += len(batch_embeddings)

    # Save to JSON file
    with open(output_file, 'w') as f:
        json.dump(transformed_dict, f, indent=4)

    print(f"Saved transformed embeddings to {output_file}")
    return transformed_dict

# Assuming `model` is your trained neural network
save_transformed_embeddings(style_classifier_trained, embeddings, "item_style.json", batch_size=32)

0 / 8159
100 / 8159
200 / 8159
300 / 8159
400 / 8159
500 / 8159
600 / 8159
700 / 8159
800 / 8159
900 / 8159
1000 / 8159
1100 / 8159
1200 / 8159
1300 / 8159
1400 / 8159
1500 / 8159
1600 / 8159
1700 / 8159
1800 / 8159
1900 / 8159
2000 / 8159
2100 / 8159
2200 / 8159
2300 / 8159
2400 / 8159
2500 / 8159
2600 / 8159
2700 / 8159
2800 / 8159
2900 / 8159
3000 / 8159
3100 / 8159
3200 / 8159
3300 / 8159
3400 / 8159
3500 / 8159
3600 / 8159
3700 / 8159
3800 / 8159
3900 / 8159
4000 / 8159
4100 / 8159
4200 / 8159
4300 / 8159
4400 / 8159
4500 / 8159
4600 / 8159
4700 / 8159
4800 / 8159
4900 / 8159
5000 / 8159
5100 / 8159
5200 / 8159
5300 / 8159
5400 / 8159
5500 / 8159
5600 / 8159
5700 / 8159
5800 / 8159
5900 / 8159
6000 / 8159
6100 / 8159
6200 / 8159
6300 / 8159
6400 / 8159
6500 / 8159
6600 / 8159
6700 / 8159
6800 / 8159
6900 / 8159
7000 / 8159
7100 / 8159
7200 / 8159
7300 / 8159
7400 / 8159
7500 / 8159
7600 / 8159
7700 / 8159
7800 / 8159
7900 / 8159
8000 / 8159
8100 / 8159
Saved transformed embeddings

{100004189: [0.0,
  0.0,
  0.0,
  32.754798889160156,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  83.06120300292969,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  98.27393341064453,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  5.189638137817383,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
 